In [3]:
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point, shape, box, Polygon
from shapely.ops import unary_union
import os
import folium
import glob
import pyproj
from pyproj import Geod, Transformer
import laspy
import numpy as np
import subprocess
import whitebox
from datetime import datetime

# Initialize WhiteboxTools
wbt = whitebox.WhiteboxTools()

# Directory paths
DEJU_las_directory = "C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/DEJU/NEON.D19.DEJU.DP1.30003.001.2018-08.basic.20240802T220020Z.RELEASE-2024/"
BONA_las_directory = "C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_smfp_discrete/"
BONA_las_normalized_directory = "C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_normalized/"

# Clipped LAS files
TEAK_clipped_las_path = "C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/clipped_las/"
BONA_clipped_las_path = "C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_las/"
BONA_6km_clipped_las_path = "C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_6km_las/"

# Define the CRS EPSG code for NEON BONA site in Alaska
BONA_CRS = 32606

def get_date_subfolder():
    current_date = datetime.now()
    return current_date.strftime('%Y_%m_%d')

def calculate_buffer_radius(group):
    if len(group) > 1:
        # Directly use the CRS from the GeoDataFrame
        gdf = gpd.GeoDataFrame(group, geometry=gpd.points_from_xy(group.easting, group.northing), crs=group.crs)

        # Calculate the centroid of the group
        centroid_easting = gdf['easting'].mean()
        centroid_northing = gdf['northing'].mean()
        centroid = Point(centroid_easting, centroid_northing)

        # Calculate distances from the centroid to each point
        distances = gdf.geometry.distance(centroid)
        max_distance = distances.max() + 10
    else:
        # For a single point, use a default buffer size
        centroid_easting = group['easting'].iloc[0]
        centroid_northing = group['northing'].iloc[0]
        max_distance = 10  # Default or minimum buffer size (e.g., 10 meters)

    return (centroid_easting, centroid_northing), max_distance

def create_buffers_from_csv(csv_file, output_folder, prefix):
    # Read the CSV file
    df = pd.read_csv(csv_file)

    # Determine UTM zone and CRS for the CSV file
    # In the future, refactor this into a function.  Seems like it can be reused.
    mean_longitude = df['longitude'].mean()
    utm_zone = int((mean_longitude + 180) // 6) + 1
    hemisphere = '326' if df['latitude'].iloc[0] >= 0 else '327'
    crs = f"EPSG:{hemisphere}{utm_zone:02d}"

    print(utm_zone)
    print(crs)
    
    # Create a GeoDataFrame
    gdf = gpd.GeoDataFrame(df, geometry=gpd.points_from_xy(df.easting, df.northing), crs=crs)

    # Ensure the output folder exists
    os.makedirs(output_folder, exist_ok=True)

    # Process each plotID_x group
    for plot_id, group in gdf.groupby('plotID_x'):
        # Calculate the buffer radius
        centroid, buffer_radius = calculate_buffer_radius(group)

        # Create a buffer around the centroid
        point = Point(centroid[0], centroid[1])
        buffered = point.buffer(buffer_radius)

        # Create a GeoDataFrame for the buffer
        buffer_gdf = gpd.GeoDataFrame(geometry=[buffered], crs=gdf.crs)

        # Save the buffer to a shapefile
        buffer_shapefile = os.path.join(output_folder, f"buffer_{prefix}_{plot_id}.shp")
        buffer_gdf.to_file(buffer_shapefile)

        print(f'Saved shapefile for group {plot_id} at {buffer_shapefile}')

def popup_construct(each_point):
    lat = round(each_point['latitude'], 4)
    long = round(each_point['longitude'], 4)
    pop = (
        'plotID: ' + str(each_point['plotID_x']) + ',<br><br>subplotID: ' + str(each_point['subplotID']) + 
        ',<br><br>individualID: ' + str(each_point['individualID']) + 
        ',<br><br>lat: ' + str(lat) + ', ' + '<br><br>long: ' + str(long)
        )
    return pop

def plot_points(df, color, map_object):
    for index, row in df.iterrows():
        # This formats the popup window with an iframe and sets its width to display
        iframe = folium.IFrame(popup_construct(row))
        popup = folium.Popup(iframe, min_width=300, max_width=300)

        if pd.notna(row['easting']):
            folium.Marker(
                location=[row['latitude'], row['longitude']],
                popup=popup,
                icon=folium.Icon(color=color)
            ).add_to(map_object)

            folium.Circle(
                location=[row['latitude'], row['longitude']],
                radius=1,
                fill=True,
                color=color
            ).add_to(map_object)


def utm_to_latlon(easting, northing, crs):
    """Convert UTM coordinates to latitude and longitude using the CRS from the shapefile."""
    # Create CRS object
    utm_crs = pyproj.CRS(crs)
    latlon_crs = pyproj.CRS(proj='latlong', ellps='WGS84')
    
    # Create a transformer for converting coordinates
    transformer = Transformer.from_crs(utm_crs, latlon_crs, always_xy=True)
    lon, lat = transformer.transform(easting, northing)
    return lat, lon

def plot_boundaries_from_shapefiles(m, shp_files, color):
    """Plot boundaries from shapefiles onto the Folium map."""
    for shp_file in shp_files:
        gdf = gpd.read_file(shp_file)

        print(f"Reading in shapefile: {shp_file}")

        # Ensure CRS is in the right format for the transformer
        crs = gdf.crs.to_string()
        print(f"crs: {crs}")
        file_name = os.path.basename(shp_file)

        for _, row in gdf.iterrows():
            geom = shape(row['geometry'])
            if geom.geom_type == 'Polygon':
                # Extract boundary coordinates
                coords = list(geom.exterior.coords)
                
                # Convert to latitude and longitude
                lat_lon_coords = [utm_to_latlon(*coord, crs) for coord in coords]

                # Create a popup with the file name
                popup = folium.Popup(file_name, parse_html=True)

                # Plot the polygon on the Folium map
                folium.Polygon(
                    locations=lat_lon_coords,
                    color='black',
                    weight=2,
                    fill=True,
                    fill_color=color,
                    popup=popup  # Add the popup to the polygon
                ).add_to(m)
                
    return m

def plot_boundaries_from_lasfiles(map_object, las_file_dir, crs_epsg):
    """Plot the bounding boxes of LAS/LAZ files on a Folium map."""
    # Retrieve bounding boxes from LAS files
    las_bboxes = get_las_bounding_boxes(las_file_dir)
    
    # Initialize the transformer for the given CRS
    transformer = Transformer.from_crs(crs_epsg, "EPSG:4326", always_xy=True)

    # Plot each bounding box
    for las_file, bbox in las_bboxes.items():
        # Convert bounding box coordinates to lat/lon
        min_x, min_y = bbox.bounds[0], bbox.bounds[1]
        max_x, max_y = bbox.bounds[2], bbox.bounds[3]
        
        min_lon, min_lat  = transformer.transform(min_x, min_y)
        max_lon, max_lat  = transformer.transform(max_x, max_y)

        # Calculate the center of the bounding box
        center_lon = (min_lon + max_lon) / 2
        center_lat = (min_lat + max_lat) / 2
    
        # Extract just the file name (not the full path)
        file_name = os.path.basename(las_file)

        # Add a rectangle to the map
        folium.Polygon(
            locations=[
                [min_lat, min_lon],
                [min_lat, max_lon],
                [max_lat, max_lon],
                [max_lat, min_lon],
                [min_lat, min_lon]
            ],
            color='blue',
            fill=True,
            fill_opacity=0.3,
            # popup=f"LAS File: {las_file}"
        ).add_to(map_object)

        # Add a marker at the center of the bounding box
        folium.Marker(
            location=[center_lat, center_lon],
            popup=file_name,
            icon=folium.Icon(color='red', icon='info-sign')
        ).add_to(map_object)
        
        # Debugging statements
        print(f"LAS File: {las_file}")
        print(f"Bounding Box (EPSG:{crs_epsg}): {bbox}")
        print(f"Converted to Lat/Lon: ({min_lat}, {min_lon}) to ({max_lat}, {max_lon})")

    return map_object

def get_las_bounding_box(las_file):
    """Get the bounding box of a LAS/LAZ file."""
    with laspy.open(las_file) as las:
        # Get the header to extract bounds
        header = las.header
        min_x, min_y, min_z = header.min
        max_x, max_y, max_z = header.max

        # Create a bounding box with the min and max coordinates
        bounding_box = {
            'min_x': min_x,
            'min_y': min_y,
            'max_x': max_x,
            'max_y': max_y
        }
        return bounding_box

def get_las_bounding_boxes(directory):
    """Get bounding boxes for all LAS/LAZ files in the specified directory."""
    las_files = glob.glob(os.path.join(directory, '*.laz'))
    laz_files = glob.glob(os.path.join(directory, '*.las'))
    all_files = las_files + laz_files
    bounding_boxes = {}

    for las_file in all_files:
        bbox = get_las_bounding_box(las_file)
        bounding_boxes[las_file] = box(bbox['min_x'], bbox['min_y'], bbox['max_x'], bbox['max_y'])
    return bounding_boxes

def get_shapefile_bounding_box(shapefile):
    """Get the bounding box of a shapefile."""
    gdf = gpd.read_file(shapefile)
    bounds = gdf.total_bounds  # returns (minx, miny, maxx, maxy)
    
    # Create a bounding box with the min and max coordinates
    bounding_box = {
        'min_x': bounds[0],
        'min_y': bounds[1],
        'max_x': bounds[2],
        'max_y': bounds[3]
    }
    return bounding_box

def get_shapefile_bounding_boxes(directory):
    """Get bounding boxes for all shapefiles in the specified directory."""
    shapefiles = glob.glob(os.path.join(directory, '*.shp'))
    bounding_boxes = {}

    for shapefile in shapefiles:
        bbox = get_shapefile_bounding_box(shapefile)
        bounding_boxes[shapefile] = box(bbox['min_x'], bbox['min_y'], bbox['max_x'], bbox['max_y'])
    return bounding_boxes

def check_shapefiles_within_las_multi(shapefile_dir, las_dir):
    """Check which shapefiles are fully within the combined bounding box of LAS files."""
    las_bboxes = get_las_bounding_boxes(las_dir)
    shapefile_bboxes = get_shapefile_bounding_boxes(shapefile_dir)
    
    # Compute the combined bounding box of all LAS files
    combined_las_bbox = unary_union(list(las_bboxes.values()))
    
    results = {}
    
    for shapefile, shp_bbox in shapefile_bboxes.items():
        # Extract just the filename from the full path
        shapefile_name = os.path.basename(shapefile)

        containing_las_files = []
        
        for las_file, las_bbox in las_bboxes.items():
            if las_bbox.intersects(shp_bbox):
                las_file_name = os.path.basename(las_file)
                containing_las_files.append(las_file_name)
        
        # Check if the shapefile's bbox is within the combined bounding box of the LAS files
        fully_within = combined_las_bbox.contains(shp_bbox)
        # Save results including bounding box information
        results[os.path.basename(shapefile_name)] = {
            'las_files': containing_las_files,
            'fully_within': fully_within,
            'shapefile_bbox': shp_bbox.bounds,  # Bounding box of the shapefile
            'combined_las_bbox': combined_las_bbox.bounds  # Bounding box of the combined LAS area
        }
    
    print(type(shp_bbox))
    print(type(combined_las_bbox))
    return results

def format_results(results):
    """Format the results into a more readable structure and export to a file if needed."""
    # Convert the results dictionary into a list of dictionaries for better readability
    formatted_results = []
    
    for shapefile, info in results.items():
        formatted_result = {
            'Shapefile': shapefile,
            'Containing LAS Files': ', '.join(info['las_files']),
            'Fully Within Combined LAS Bounding Box': info['fully_within'],
            'Shapefile Bounding Box (min_x, min_y, max_x, max_y)': info['shapefile_bbox'],
            'Combined LAS Bounding Box (min_x, min_y, max_x, max_y)': info['combined_las_bbox']
        }
        formatted_results.append(formatted_result)
    
    # Create a DataFrame for better readability
    df_results = pd.DataFrame(formatted_results)
    
    # Print the results
    print(df_results.to_string(index=False))
    
    # Optionally, export the results to a CSV file
    csv_path = 'shapefile_check_results.csv'
    df_results.to_csv(csv_path, index=False)
    print(f'Results exported to {csv_path}')

def clip_las_to_shp_multi(results, shapefile_dir, las_dir, output_dir):
    """Clip LAS files based on shapefile results."""
    # Create the directory for the output file if it does not exist
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)
        print(f"Created output directory: {output_dir}")
    
    for shapefile, info in results.items():
        shapefile_path = os.path.join(shapefile_dir, shapefile)
        containing_las_files = info['las_files']
        output_file = os.path.join(output_dir, f"clipped_{shapefile}.las")

        try:
            if len(containing_las_files) == 1:
                # Only one LAS file - Clip directly
                las_file = os.path.join(las_dir, containing_las_files[0])
                
                # Perform clipping
                clip_lidar_with_shapefile(las_file, shapefile_path, output_file)
                print(f"Clipped {las_file} to {output_file} using {shapefile_path}")

            else:
                # Multiple LAS files - Merge first, then clip
                merged_file = os.path.join(output_dir, f"merged_{shapefile}.las")
                
                # Merge LAS files
                merge_las_files_with_lastools([os.path.join(las_dir, las_file) for las_file in containing_las_files], merged_file)
                print(f"Merged LAS files into {merged_file}")

                # Perform clipping on the merged file
                clip_lidar_with_shapefile(merged_file, shapefile_path, output_file)
                print(f"Clipped {merged_file} to {output_file} using {shapefile_path}")

                # Remove the merged LAS file after clipping
                os.remove(merged_file)
                print(f"Removed merged file: {merged_file}")

        except Exception as e:
            print(f"Error processing {shapefile}: {e}")

    print("Processing complete.")

def normalize_path(path):
    """Replace all forward slashes with backslashes in the given path."""
    return path.replace('/', '\\')

def run_command(command, args):
    """Run a command with subprocess and handle paths."""
    cmd_list = [command] + args
    print("Running command:", ' '.join(cmd_list))  # Print the full command for debugging

    try:
        result = subprocess.run(cmd_list, capture_output=True, text=True, check=True)
        print("Command output:")
        print(result.stdout)
    except subprocess.CalledProcessError as e:
        print("Error during command execution:")
        print(e.stderr)
        print(f"Exit status: {e.returncode}")
        
def merge_las_files_with_lastools(input_files, output_file):
    """Merge LAS files using LAStools' lasmerge64.exe."""
    
    # Ensure the output directory exists
    output_dir = os.path.dirname(output_file)
    os.makedirs(output_dir, exist_ok=True)

    # Prepare the command arguments
    command = "lasmerge64.exe"
    args = ['-i'] + input_files + ['-o', output_file]

    # Run the command
    run_command(command, args)

def clip_lidar_with_shapefile(input_las_file, shapefile, output_las_file):
    """ Clip a .las file with a shapefile using WhiteboxTools. """
    
    # Set the working directory
    wbt.set_working_dir(os.path.dirname(input_las_file))
    
    # Perform the clipping
    wbt.clip_lidar_to_polygon(
        i=input_las_file,
        polygons=shapefile,
        output=output_las_file
    )
    
    print(f"Clipped {input_las_file} with {shapefile} to {output_las_file}.")

In [3]:
# Define your parameters
TEAK_100_file = "C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/TEAK_entries_perplot_100.csv"
TEAK_400_file = "C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/TEAK_entries_perplot_400.csv"
TEAK_shapefile_folder = "C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers"

# Create buffers from the CSV files
create_buffers_from_csv(TEAK_100_file, TEAK_shapefile_folder, "100")
create_buffers_from_csv(TEAK_400_file, TEAK_shapefile_folder, "400")

11
EPSG:32611
Saved shapefile for group TEAK_001 at C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_001.shp
Saved shapefile for group TEAK_002 at C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_002.shp
Saved shapefile for group TEAK_003 at C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_003.shp
Saved shapefile for group TEAK_005 at C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_005.shp
Saved shapefile for group TEAK_006 at C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_006.shp
Saved shapefile for group TEAK_007 at C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_007.shp
Saved shapefile for group TEAK_010 at C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_010.shp
Saved 

In [4]:
output_html_path = "C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/TEAK_100_vs_400_withBuffers.html"

# Initialize the map
m = folium.Map(location=[37.00583, -119.00602], zoom_start=12)

# Read the CSV files
merged_100_df = pd.read_csv(TEAK_100_file)
merged_400_df = pd.read_csv(TEAK_400_file)

# Plot points
# plot_points(merged_100_df, 'red', m)
# plot_points(merged_400_df, 'blue', m)

# Retrieve shapefiles from the output folder
TEAK_shp_files = glob.glob(os.path.join(TEAK_shapefile_folder, '*.shp'))

# Plot boundaries from shapefiles
plot_boundaries_from_shapefiles(m, TEAK_shp_files)

# Save the map
m.save(output_html_path)
m

Reading in shapefile: C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_001.shp
Reading in shapefile: C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_002.shp
Reading in shapefile: C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_003.shp
Reading in shapefile: C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_005.shp
Reading in shapefile: C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_006.shp
Reading in shapefile: C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_007.shp
Reading in shapefile: C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_010.shp
Reading in shapefile: C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_011.shp
Reading 

In [4]:
def check_shapefiles_within_las(shapefiles, las_bounding_boxes):
    """Check which shapefiles are fully within the bounding boxes of LAS/LAZ files."""
    
    fully_within_files = []  # List to keep track of tuples (shapefile, LAS file)
    not_fully_within_files = set()  # Set to keep track of shapefiles not fully within any LAS file

    for shp_file in shapefiles:
        shp_gdf = gpd.read_file(shp_file)
        shp_bounds = shp_gdf.total_bounds  # Get bounding box of shapefile
        shp_box = box(shp_bounds[0], shp_bounds[1], shp_bounds[2], shp_bounds[3])

        is_fully_within = False
        
        for las_file, las_box in las_bounding_boxes.items():
            if shp_box.within(las_box):
                fully_within_files.append((shp_file, las_file))
                is_fully_within = True
                break
        
        if not is_fully_within:
            not_fully_within_files.add(shp_file)
    
    if not_fully_within_files:
        print("\nShapefiles not fully within any LAS file:")
        for shp_file in not_fully_within_files:
            print(os.path.basename(shp_file))
    
    return fully_within_files, list(not_fully_within_files)

def decompress_laz(laz_file, las_file):
    """ Decompress a .laz file to a .las file using LAStools. """
    try:
        subprocess.run([
            'laszip64.exe',  # Path to the laszip64.exe executable
            '-i', laz_file,
            '-o', las_file
        ], check=True)
        print(f"Decompressed {laz_file} to {las_file}.")
    except subprocess.CalledProcessError as e:
        print(f"Error decompressing {laz_file}: {e}")

def process_files(fully_within_files, clipped_las_path):
    if not os.path.exists(clipped_las_path):
        os.makedirs(clipped_las_path)

    for shp_file, laz_file in fully_within_files:
        temp_las_file = laz_file

        if laz_file.endswith('.laz'):
            temp_las_file = os.path.join(clipped_las_path, f"temp_{os.path.basename(laz_file).replace('.laz', '.las')}")
            # Decompress the .laz file to a .las file
            decompress_laz(laz_file, temp_las_file)
        
        output_file = os.path.join(
            clipped_las_path, 
            f'clipped_{os.path.basename(shp_file).replace(".shp", ".las")}'
        )

        # temp_las_file = os.path.join(clipped_las_path, f"temp_{os.path.basename(laz_file).replace('.laz', '.las')}")
        # output_file = os.path.join(
        #     clipped_las_path, 
        #     f'clipped_{os.path.basename(shp_file).replace(".shp", ".las")}'
        # )

        # # Decompress the .laz file to a .las file
        # decompress_laz(laz_file, temp_las_file)

        # Clip the .las file with the shapefile using WhiteboxTools
        clip_lidar_with_shapefile(temp_las_file, shp_file, output_file)

        # Remove the temporary .las file
        if os.path.exists(temp_las_file):
            os.remove(temp_las_file)
            print(f'Removed temporary file {temp_las_file}.')



In [8]:
# Directory paths
TEAK_las_directory = "C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_lidar-point-cloud-line/NEON.D17.TEAK.DP1.30003.001.2023-07.basic.20240409T221345Z.PROVISIONAL/"

TEAK_las_bounding_boxes = get_las_bounding_boxes(TEAK_las_directory)

print(TEAK_las_bounding_boxes)

# Check shapefiles with LAS files
fully_within_files, not_fully_within_files = check_shapefiles_within_las(TEAK_shp_files, TEAK_las_bounding_boxes)

print(len(TEAK_shp_files))
print(not_fully_within_files)
print(len(not_fully_within_files))
print(fully_within_files)
print(len(fully_within_files))


{'C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_lidar-point-cloud-line/NEON.D17.TEAK.DP1.30003.001.2023-07.basic.20240409T221345Z.PROVISIONAL\\NEON_D17_TEAK_DP1_312000_4091000_classified_point_cloud_colorized.laz': <POLYGON ((312999.999 4091286.88, 312999.999 4091999.997, 312810.551 4091999...>, 'C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_lidar-point-cloud-line/NEON.D17.TEAK.DP1.30003.001.2023-07.basic.20240409T221345Z.PROVISIONAL\\NEON_D17_TEAK_DP1_312000_4092000_classified_point_cloud_colorized.laz': <POLYGON ((312999.999 4092000.002, 312999.999 4092999.999, 312753.043 409299...>, 'C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_lidar-point-cloud-line/NEON.D17.TEAK.DP1.30003.001.2023-07.basic.20240409T221345Z.PROVISIONAL\\NEON_D17_TEAK_DP1_312000_4093000_classified_point_cloud_colorized.laz': <POLYGON ((312999.999 4093000, 312999.999 4093999.997, 312855.831 4093999.99...>, 'C:/Users/allen/OneDrive/Desktop/Work/d

In [9]:
process_files(fully_within_files, TEAK_clipped_las_path)

Decompressed C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_lidar-point-cloud-line/NEON.D17.TEAK.DP1.30003.001.2023-07.basic.20240409T221345Z.PROVISIONAL\NEON_D17_TEAK_DP1_320000_4094000_classified_point_cloud_colorized.laz to C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/clipped_las/temp_NEON_D17_TEAK_DP1_320000_4094000_classified_point_cloud_colorized.las.
.\whitebox_tools.exe --run="ClipLidarToPolygon" --wd="C:\Users\allen\OneDrive\Desktop\Work\data\Tree Segmentation\TEAK\clipped_las" --input='C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/clipped_las/temp_NEON_D17_TEAK_DP1_320000_4094000_classified_point_cloud_colorized.las' --polygons='C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/buffers\buffer_100_TEAK_001.shp' --output='C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/clipped_las/clipped_buffer_100_TEAK_001.las' -v --compress_rasters=False

*********************************
* Wel

KeyboardInterrupt: 

In [5]:
def calculate_offset_point(lat, lon, bearing, distance_m):
    """Calculate a point offset from the original point by a given bearing and distance."""
    geod = Geod(ellps="WGS84")
    lon2, lat2, _ = geod.fwd(lon, lat, bearing, distance_m)
    return lon2, lat2

def get_utm_crs(latitude, longitude):
    """Determine UTM zone and CRS for a given latitude and longitude."""
    utm_zone = int((longitude + 180) // 6) + 1
    hemisphere = '326' if latitude >= 0 else '327'
    crs = f"EPSG:{hemisphere}{utm_zone:02d}"
    return crs

def convert_to_utm(lon, lat, crs):
    """Convert latitude and longitude to easting and northing in the given CRS."""
    transformer = Transformer.from_crs("EPSG:4326", crs, always_xy=True)
    print(f"lat: {lat}, long: {lon}")
    easting, northing = transformer.transform(lon, lat)
    print(f"easting: {easting}, northing: {northing}")
    return easting, northing

def create_rectangle(lat1, lon1, lat2, lon2, width_m):
    """Create a rectangle polygon for the segment from (lat1, lon1) to (lat2, lon2) with a given width in meters."""
    geod = Geod(ellps="WGS84")
    bearing, _, _ = geod.inv(lon1, lat1, lon2, lat2)
    
    left_bearing = (bearing - 90) % 360
    right_bearing = (bearing + 90) % 360
    
    p1_left = calculate_offset_point(lat1, lon1, left_bearing, width_m / 2)
    p1_right = calculate_offset_point(lat1, lon1, right_bearing, width_m / 2)
    p2_left = calculate_offset_point(lat2, lon2, left_bearing, width_m / 2)
    p2_right = calculate_offset_point(lat2, lon2, right_bearing, width_m / 2)

    # Determine CRS based on the first point
    crs = get_utm_crs(lat1, lon1)
    # print(f"crs: {crs}")

    # Convert points to easting and northing in the determined CRS
    p1_left_utm = convert_to_utm(*p1_left, crs)
    p1_right_utm = convert_to_utm(*p1_right, crs)
    p2_left_utm = convert_to_utm(*p2_left, crs)
    p2_right_utm = convert_to_utm(*p2_right, crs)
    
    # Create and return the polygon in easting and northing along with the CRS
    polygon = Polygon([p1_left_utm, p2_left_utm, p2_right_utm, p1_right_utm, p1_left_utm])
    return polygon, crs


def plot_line_segments(df, map_object):
    """Plot line segments on a Folium map using start and end latitude/longitude coordinates from the DataFrame."""
    for _, row in df.iterrows():
        # Extract start and end coordinates
        start_coords = (row['start_lat'], row['start_lon'])
        end_coords = (row['end_lat'], row['end_lon'])

        # print(f"start_coords: {start_coords}")
        # print(f"end_coords: {end_coords}")
        
        # Create a line segment
        folium.PolyLine(
            locations=[start_coords, end_coords],
            color='blue',
            weight=2,
            opacity=0.7
        ).add_to(map_object)

    return map_object

def plot_rectangles(df, map_object):
    """Plot rectangles and their points on a Folium map, including original points and rectangle vertices."""
    for _, row in df.iterrows():
        segment_id = row['segment_id']
        
        # Plot original points
        start_coords = (row['start_lat'], row['start_lon'])
        end_coords = (row['end_lat'], row['end_lon'])
        
        # Plot start and end points in red
        folium.Marker(
            start_coords,
            popup=f"Start Point - Segment {segment_id}<br>Lat={start_coords[0]}, Lon={start_coords[1]}",
            icon=folium.Icon(color='red', icon='info-sign')
        ).add_to(map_object)
        
        folium.Marker(
            end_coords,
            popup=f"End Point - Segment {segment_id}<br>Lat={end_coords[0]}, Lon={end_coords[1]}",
            icon=folium.Icon(color='red', icon='info-sign')
        ).add_to(map_object)
        
        # Create rectangle and plot its points
        rectangle, crs = create_rectangle(row['start_lat'], row['start_lon'], row['end_lat'], row['end_lon'], width_m=10)
        rectangle_coords = list(rectangle.exterior.coords)

        print(rectangle_coords)
        print(crs)
        # Initialize transformer with the correct CRS
        transformer = Transformer.from_crs(crs, "EPSG:4326", always_xy=True)

        # Plot rectangle vertices in blue
        for idx, coord in enumerate(rectangle_coords):
            easting, northing = coord[0], coord[1]
            lon, lat = transformer.transform(easting, northing)
            print(f"Rectangle Point {idx + 1}: Lat={lat}, Lon={lon}")
            folium.Marker(
                [lat, lon],
                popup=f"Rectangle Point {idx + 1} - Segment {segment_id}<br>Lat={lat}, Lon={lon}",
                icon=folium.Icon(color='blue', icon='info-sign')
            ).add_to(map_object)

    return map_object

In [11]:
BONA_input_file = "C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/segment_coordinates.csv"

# Ensure the output directory exists
BONA_shapefile_dir = 'C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/BONA_segment_shapefiles'
os.makedirs(BONA_shapefile_dir, exist_ok=True)

# Read the CSV file
BONA_df = pd.read_csv(BONA_input_file)

# Convert date columns to datetime with fractional seconds
BONA_df['start_time'] = pd.to_datetime(BONA_df['start_time'], format='%Y-%m-%d %H:%M:%S.%f')
BONA_df['end_time'] = pd.to_datetime(BONA_df['end_time'], format='%Y-%m-%d %H:%M:%S.%f')

# Process each row in the DataFrame
for idx, row in BONA_df.iterrows():
    segment_id = row['segment_id']
    start_lat, start_lon = row['start_lat'], row['start_lon']
    end_lat, end_lon = row['end_lat'], row['end_lon']
    start_time = row['start_time']
    end_time = row['end_time']

    # Format the times with four decimal places for seconds
    start_time_formatted = start_time.strftime('%Y-%m-%d_%H-%M-%S-%f')[:-3]
    end_time_formatted = end_time.strftime('%Y-%m-%d_%H-%M-%S-%f')[:-3]

    print(f"segment_id: {segment_id}")
    print(f"start_lat, start_lon: {start_lat}, {start_lon}")
    print(f"end_lat, end_lon: {end_lat}, {end_lon}")
    print(f"start_time: {start_time}")
    print(f"end_time: {end_time}")
    
    rectangle, crs = create_rectangle(start_lat, start_lon, end_lat, end_lon, 10)
    
    print(rectangle)
    # Create a GeoDataFrame with the coordinates in UTM
    gdf = gpd.GeoDataFrame({'segment_id': [segment_id], 'geometry': [rectangle]}, crs=crs)

    # Define the output shapefile path
    shapefile_path = os.path.join(BONA_shapefile_dir, f'segment_{segment_id}_start_{start_time_formatted}_end_{end_time_formatted}.shp')
    
    print(shapefile_path)
    # Save the GeoDataFrame to a shapefile
    gdf.to_file(shapefile_path, driver='ESRI Shapefile')

print("Individual shapefiles creation complete.")

segment_id: 362294
start_lat, start_lon: 65.13238503827168, -147.49236304568657
end_lat, end_lon: 65.1330104619874, -147.49250962613877
start_time: 2019-09-11 09:15:16.357455104
end_time: 2019-09-11 09:15:16.367355136
lat: 65.1323806346054, long: -147.49246904547402
easting: 476891.97970318096, northing: 7223298.374210075
lat: 65.13238944186305, long: -147.49225704586402
easting: 476901.93480887415, northing: 7223299.2781973565
lat: 65.13300605832147, long: -147.49261562841968
easting: 476885.64546271175, northing: 7223368.129668197
lat: 65.13301486557839, long: -147.49240362382275
easting: 476895.6005705758, northing: 7223369.033631984
POLYGON ((476891.97970318096 7223298.374210075, 476885.64546271175 7223368.129668197, 476895.6005705758 7223369.033631984, 476901.93480887415 7223299.2781973565, 476891.97970318096 7223298.374210075))
C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/BONA_segment_shapefiles\segment_362294_start_2019-09-11_09-15-16-357_end_2019-09-11_

In [8]:
BONA_input_file_2 = "C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/20m_segment_coordinates.csv"

# Ensure the output directory exists
BONA_shapefile_dir_2 = 'C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/BONA_6km_segment_shapefiles'

if not os.path.exists(BONA_shapefile_dir_2):
    os.makedirs(BONA_shapefile_dir_2)
    
# Read the CSV file
BONA_df2 = pd.read_csv(BONA_input_file_2)

# Process each row in the DataFrame
for idx, row in BONA_df2.iterrows():
    segment_id = row['segment_id']
    start_lat, start_lon = row['lat_start'], row['lon_start']
    end_lat, end_lon = row['lat_end'], row['lon_end']

    print(f"segment_id: {segment_id}")
    print(f"start_lat, start_lon: {start_lat}, {start_lon}")
    print(f"end_lat, end_lon: {end_lat}, {end_lon}")
    
    rectangle, crs = create_rectangle(start_lat, start_lon, end_lat, end_lon, 10)
    
    print(rectangle)
    # Create a GeoDataFrame with the coordinates in UTM
    gdf = gpd.GeoDataFrame({'segment_id': [segment_id], 'geometry': [rectangle]}, crs=crs)

    # Define the output shapefile path
    shapefile_path = os.path.join(BONA_shapefile_dir_2, f'segment_{segment_id}.shp')
    
    print(shapefile_path)
    # Save the GeoDataFrame to a shapefile
    gdf.to_file(shapefile_path, driver='ESRI Shapefile')

print("Individual shapefiles creation complete.")

segment_id: 362209.0
start_lat, start_lon: 65.12097322965823, -147.41781977020676
end_lat, end_lon: 65.12115161326629, -147.41786532670318
lat: 65.12096843333339, long: -147.41792562839
easting: 480381.3041373141, northing: 7222001.294679024
lat: 65.12097802590833, long: -147.41771391198535
easting: 480391.2497042588, northing: 7222002.298001367
lat: 65.12114681694156, long: -147.41797118559626
easting: 480379.2971396219, northing: 7222021.18931304
lat: 65.12115640951629, long: -147.41775946777193
easting: 480389.24270730925, northing: 7222022.192628116
POLYGON ((480381.3041373141 7222001.294679024, 480379.2971396219 7222021.18931304, 480389.24270730925 7222022.192628116, 480391.2497042588 7222002.298001367, 480381.3041373141 7222001.294679024))
C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/BONA_6km_segment_shapefiles\segment_362209.0.shp
segment_id: 362345.0
start_lat, start_lon: 65.14196286873732, -147.4930199853601
end_lat, end_lon: 65.14214574937604, -147.49

In [7]:
BONA_input_file_3 = "C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/10km_segment_coordinates.csv"

# Ensure the output directory exists
BONA_shapefile_dir_2 = 'C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/BONA_6km_segment_shapefiles'
date_subfolder = get_date_subfolder()

# Define the output shapefile path
shapefile_path_3 = os.path.join(BONA_shapefile_dir_2, date_subfolder)

if not os.path.exists(shapefile_path_3):
    os.makedirs(shapefile_path_3)
# Read the CSV file
BONA_df3 = pd.read_csv(BONA_input_file_3)

# Process each row in the DataFrame
for idx, row in BONA_df3.iterrows():
    segment_id = row['segment_id']
    start_lat, start_lon = row['lat_start'], row['lon_start']
    end_lat, end_lon = row['lat_end'], row['lon_end']

    print(f"segment_id: {segment_id}")
    print(f"start_lat, start_lon: {start_lat}, {start_lon}")
    print(f"end_lat, end_lon: {end_lat}, {end_lon}")
    
    rectangle, crs = create_rectangle(start_lat, start_lon, end_lat, end_lon, 10)
    
    print(rectangle)
    # Create a GeoDataFrame with the coordinates in UTM
    gdf = gpd.GeoDataFrame({'segment_id': [segment_id], 'geometry': [rectangle]}, crs=crs)

    shapefile_file_path = os.path.join(shapefile_path_3, f'segment_{segment_id}.shp')
    
    # Save the GeoDataFrame to a shapefile
    gdf.to_file(shapefile_file_path, driver='ESRI Shapefile')
    print(f"shapefile saved to: {shapefile_file_path}")

print("Individual shapefiles creation complete.")

segment_id: 362209.0
start_lat, start_lon: 65.12097322965823, -147.41781977020676
end_lat, end_lon: 65.12115161326629, -147.41786532670318
lat: 65.12096843333339, long: -147.41792562839
easting: 480381.3041373141, northing: 7222001.294679024
lat: 65.12097802590833, long: -147.41771391198535
easting: 480391.2497042588, northing: 7222002.298001367
lat: 65.12114681694156, long: -147.41797118559626
easting: 480379.2971396219, northing: 7222021.18931304
lat: 65.12115640951629, long: -147.41775946777193
easting: 480389.24270730925, northing: 7222022.192628116
POLYGON ((480381.3041373141 7222001.294679024, 480379.2971396219 7222021.18931304, 480389.24270730925 7222022.192628116, 480391.2497042588 7222002.298001367, 480381.3041373141 7222001.294679024))
shapefile saved to: C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/BONA_6km_segment_shapefiles\2024_09_13\segment_362209.0.shp
segment_id: 362345.0
start_lat, start_lon: 65.14196286873732, -147.4930199853601
end_lat, end_

In [9]:
# Calculate mean latitude and longitude for initial map center
# mean_latitude = BONA_df[['start_lat', 'end_lat']].mean().mean()
# mean_longitude = BONA_df[['start_lon', 'end_lon']].mean().mean()
mean_latitude = BONA_df3[['lat_start', 'lat_end']].mean().mean()
mean_longitude = BONA_df3[['lon_start', 'lon_end']].mean().mean()

# Initialize the map
m = folium.Map(location=[mean_latitude, mean_longitude], zoom_start=12)

# # Plot the line segments from the df
# plot_line_segments(BONA_df, m)
# plot_rectangles(BONA_df, m)

# Retrieve shapefiles from the output folder
# shp_files = glob.glob(os.path.join(BONA_shapefile_dir, '*.shp'))
# shp_files_2 = glob.glob(os.path.join(BONA_shapefile_dir_2, '*.shp'))
shp_files_3 = glob.glob(os.path.join(shapefile_path_3, '*.shp'))

# Plot boundaries from shapefiles
plot_boundaries_from_lasfiles(m, BONA_las_directory, BONA_CRS)
# plot_boundaries_from_shapefiles(m, shp_files, 'red')
# plot_boundaries_from_shapefiles(m, shp_files_2, 'blue')
plot_boundaries_from_shapefiles(m, shp_files_3, 'blue')

m.save('BONA_segments_within_LAS_tiles.html')

m

LAS File: C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_smfp_discrete\NEON_D19_BONA_DP1_468000_7221000_classified_point_cloud_colorized.las
Bounding Box (EPSG:32606): POLYGON ((468999.99 7221316.23, 468999.99 7221999.99, 468081.96 7221999.99, 468081.96 7221316.23, 468999.99 7221316.23))
Converted to Lat/Lon: (65.11386287622793, -147.67975622146054) to (65.12008498384039, -147.66035885086796)
LAS File: C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_smfp_discrete\NEON_D19_BONA_DP1_468000_7222000_classified_point_cloud_colorized.las
Bounding Box (EPSG:32606): POLYGON ((468999.99 7222000, 468999.99 7222999.99, 468076.95 7222999.99, 468076.95 7222000, 468999.99 7222000))
Converted to Lat/Lon: (65.11999719054455, -147.68001969223542) to (65.12905703033408, -147.6605816538426)
LAS File: C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_smfp_discrete\NEON_D19_BONA_DP1_468000_7223000_classified_point_cloud_coloriz

In [7]:
### This code is deprecated.  Instead of saving lat, lon to shapefile, I'm saving the projected crs in easting, northing.
### This makes the code for comparing bounding boxes of the shapefile and the las files easier

def extract_points_from_shapefile(shapefile_path):
    """Extract latitude and longitude points from polygons in a shapefile."""
    try:
        gdf = gpd.read_file(shapefile_path)
        
        # Print CRS details for debugging
        # print(f"CRS details for {shapefile_path}:")
        # print_crs_details(gdf)
        
        latitudes = []
        longitudes = []

        for _, row in gdf.iterrows():
            geom = shape(row['geometry'])
            
            if geom.geom_type == 'Point':
                # Extract coordinates
                lon, lat = geom.x, geom.y
                
                latitudes.append(lat)
                longitudes.append(lon)
            
            elif geom.geom_type == 'Polygon':
                # Extract points from the polygon
                coords = list(geom.exterior.coords)
                
                # Extract lat/lon from the polygon points
                latitudes.extend([coord[1] for coord in coords])
                longitudes.extend([coord[0] for coord in coords])

        return latitudes, longitudes
    
    except Exception as e:
        print(f"Error in reading shapefile or extracting coordinates: {e}")
        return [], []

def create_folium_map_with_shapefiles(shapefile_folder):
    """Create a Folium map with points and polygons from all shapefiles in the given directory."""
    # Initialize the Folium map
    folium_map = folium.Map(location=[0, 0], zoom_start=2)

    all_latitudes = []
    all_longitudes = []
    
    # Retrieve all shapefiles from the directory
    shapefile_paths = glob.glob(os.path.join(shapefile_folder, '*.shp'))

    for shapefile_path in shapefile_paths:
        # Read and plot polygons
        gdf = gpd.read_file(shapefile_path)
        
        # Plot polygons on the map
        for _, row in gdf.iterrows():
            geom = shape(row['geometry'])
            
            if geom.geom_type == 'Polygon':
                geojson = folium.GeoJson(
                    geom,
                    style_function=lambda x: {'color': 'blue', 'fillOpacity': 0.2},
                    popup=f"Polygon from {os.path.basename(shapefile_path)}"
                )
                geojson.add_to(folium_map)
        
        # Extract points from the shapefile
        latitudes, longitudes = extract_points_from_shapefile(shapefile_path)
        
        if latitudes and longitudes:
            # Add points to the map with labels
            for idx, (lat, lon) in enumerate(zip(latitudes, longitudes)):
                print(f"Adding Point {idx + 1} from {shapefile_path} to map: Lat={lat}, Lon={lon}")
                folium.Marker(
                    [lat, lon],
                    popup=f"Point {idx + 1}<br>Lat={lat}, Lon={lon}<br>File: {os.path.basename(shapefile_path)}",
                    icon=folium.Icon(color='blue', icon='info-sign')
                ).add_to(folium_map)
            
            # Collect all lat/lon for adjusting the map's center and zoom
            all_latitudes.extend(latitudes)
            all_longitudes.extend(longitudes)

    if all_latitudes and all_longitudes:
        # Adjust the map bounds dynamically based on the extent of the points
        bounds = [[min(all_latitudes), min(all_longitudes)], [max(all_latitudes), max(all_longitudes)]]
        folium_map.fit_bounds(bounds)
    
    return folium_map

In [11]:
# bbox_results = check_shapefiles_within_las_multi(BONA_shapefile_dir, BONA_las_directory)
# bbox_results_2 = check_shapefiles_within_las_multi(BONA_shapefile_dir_2, BONA_las_directory)
bbox_results_3 = check_shapefiles_within_las_multi(shapefile_path_3, BONA_las_directory
)
print (len(bbox_results_3))
format_results(bbox_results_3)

<class 'shapely.geometry.polygon.Polygon'>
<class 'shapely.geometry.multipolygon.MultiPolygon'>
77
           Shapefile                                                  Containing LAS Files  Fully Within Combined LAS Bounding Box                             Shapefile Bounding Box (min_x, min_y, max_x, max_y) Combined LAS Bounding Box (min_x, min_y, max_x, max_y)
segment_362131.0.shp                                                                                                         False   (471550.5191588815, 7220918.929552503, 471563.88653112226, 7220956.620343235)         (468076.95, 7221167.63, 484315.24, 7235887.23)
segment_362135.0.shp                                                                                                         False   (471542.65321366634, 7220998.83405682, 471556.39685926103, 7221038.788534204)         (468076.95, 7221167.63, 484315.24, 7235887.23)
segment_362138.0.shp                                                                                   

In [12]:
shapefile_date_path = os.path.join(BONA_6km_clipped_las_path, date_subfolder)
clip_las_to_shp_multi(bbox_results_3, shapefile_path_3, BONA_las_normalized_directory, shapefile_date_path)

Created output directory: C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_6km_las/2024_09_13
Running command: lasmerge64.exe -i -o C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_6km_las/2024_09_13\merged_segment_362131.0.shp.las
Error during command execution:
ERROR: no input specified

Exit status: 3
Merged LAS files into C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_6km_las/2024_09_13\merged_segment_362131.0.shp.las
.\whitebox_tools.exe --run="ClipLidarToPolygon" --wd="C:\Users\allen\OneDrive\Desktop\Work\data\Tree Segmentation\BONA\clipped_6km_las\2024_09_13" --input='C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_6km_las/2024_09_13\merged_segment_362131.0.shp.las' --polygons='C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/BONA_6km_segment_shapefiles\2024_09_13\segment_362131.0.shp' --output='C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/c

In [52]:
input_files = [
    "C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_smfp_discrete/NEON_D19_BONA_DP1_476000_7223000_classified_point_cloud_colorized.las",
    "C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_smfp_discrete/NEON_D19_BONA_DP1_477000_7223000_classified_point_cloud_colorized.las"
]

output_file = "C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_las/merged_segment_362284_start_2019-09-11_09-15-16-674_end_2019-09-11_09-15-16-688.shp.las"

merge_las_files_with_lastools(input_files, output_file)

Running command: lasmerge64.exe -i C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_smfp_discrete/NEON_D19_BONA_DP1_476000_7223000_classified_point_cloud_colorized.las C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_smfp_discrete/NEON_D19_BONA_DP1_477000_7223000_classified_point_cloud_colorized.las -o C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_las/merged_segment_362284_start_2019-09-11_09-15-16-674_end_2019-09-11_09-15-16-688.shp.las
Command output:



In [24]:
clip_las_to_shp_multi(bbox_results, BONA_shapefile_dir, BONA_las_normalized_directory, BONA_clipped_las_path)
clip_las_to_shp_multi(bbox_results_2, BONA_shapefile_dir_2, BONA_las_normalized_directory, BONA_6km_clipped_las_path)

Created output directory: C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_las/
Running command: lasmerge64.exe -i C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_normalized/NEON_D19_BONA_DP1_476000_7223000_classified_point_cloud_colorized.las C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_normalized/NEON_D19_BONA_DP1_477000_7223000_classified_point_cloud_colorized.las -o C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_las/merged_segment_362284_start_2019-09-11_09-15-16-674_end_2019-09-11_09-15-16-688.shp.las
Command output:

Merged LAS files into C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/clipped_las/merged_segment_362284_start_2019-09-11_09-15-16-674_end_2019-09-11_09-15-16-688.shp.las
.\whitebox_tools.exe --run="ClipLidarToPolygon" --wd="C:\Users\allen\OneDrive\Desktop\Work\data\Tree Segmentation\BONA\clipped_las" --input='C:/Users/allen/OneDrive/Desktop/Work

In [12]:
import simplekml
from datetime import datetime

# Create a KML object
kml = simplekml.Kml()

# Convert start_time and end_time to datetime
BONA_df['start_time'] = pd.to_datetime(BONA_df['start_time'])
BONA_df['end_time'] = pd.to_datetime(BONA_df['end_time'])

# Process each row in the DataFrame
for idx, row in BONA_df.iterrows():
    segment_id = row['segment_id']
    start_lat, start_lon = row['start_lat'], row['start_lon']
    end_lat, end_lon = row['end_lat'], row['end_lon']
    start_time = row['start_time']
    end_time = row['end_time']
    
    # Format the times with four decimal places for seconds
    start_time_formatted = start_time.strftime('%Y-%m-%dT%H%M%S.') + f"{start_time.microsecond // 10000:04d}"
    end_time_formatted = end_time.strftime('%Y-%m-%dT%H%M%S.') + f"{end_time.microsecond // 10000:04d}"
    
    # Create a line for each segment
    line = kml.newlinestring(name=f"Segment {segment_id}")
    line.coords = [(start_lon, start_lat), (end_lon, end_lat)]
    line.altitudemode = simplekml.AltitudeMode.clamptoground
    line.timestamp.when = start_time_formatted
    line.extendeddata.newdata(name="end_time", value=end_time_formatted)
    
    # Add start and end points as placemarks
    start_point = kml.newpoint(name=f"Start Segment {segment_id}", coords=[(start_lon, start_lat)])
    start_point.timestamp.when = start_time_formatted
    
    end_point = kml.newpoint(name=f"End Segment {segment_id}", coords=[(end_lon, end_lat)])
    end_point.timestamp.when = end_time_formatted

# Save the KML file
kml.save("BONA_segments.kml")

print("KML file created successfully.")

KML file created successfully.


In [56]:
def process_lidar_directory(input_dir, output_dir, radius=10.0):
    """Normalize LiDAR files in a directory using the top-hat transform."""
    
    # Initialize WhiteboxTools
    wbt = whitebox.WhiteboxTools()

    # Create output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)
    
    # Iterate through all .las files in the input directory
    for filename in os.listdir(input_dir):
        if filename.lower().endswith('.las'):
            input_file = os.path.join(input_dir, filename)
            output_file = os.path.join(output_dir, filename)
            
            # Apply the top-hat transform
            try:
                print(f"Processing {input_file}...")
                wbt.lidar_tophat_transform(
                    input_file, 
                    output_file, 
                    radius=radius
                )
                print(f"Saved normalized file to {output_file}")
            except Exception as e:
                print(f"Error processing {input_file}: {e}")

    print("Normalization complete.")

process_lidar_directory(BONA_las_directory, BONA_las_normalized_directory)

Processing C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_smfp_discrete/NEON_D19_BONA_DP1_468000_7221000_classified_point_cloud_colorized.las...
.\whitebox_tools.exe --run="LidarTophatTransform" --input='C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_smfp_discrete/NEON_D19_BONA_DP1_468000_7221000_classified_point_cloud_colorized.las' --output='C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/BONA/BONA_2019_normalized/NEON_D19_BONA_DP1_468000_7221000_classified_point_cloud_colorized.las' --radius=10.0 -v --compress_rasters=False

***********************************


* Welcome to LidarTophatTransform *
* Powered by WhiteboxTools        *
* www.whiteboxgeo.com             *
***********************************
reading input LiDAR file...
Performing analysis...
Binning points: 0%
Binning points: 1%
Binning points: 2%
Binning points: 3%
Binning points: 4%
Binning points: 5%
Binning points: 6%
Binning points: 7%
Binning points: 8%
Binning points: 9%
Binning points: 10%
Binning points: 11%
Binning points: 12%
Binning points: 13%
Binning points: 14%
Binning points: 15%
Binning points: 16%
Binning points: 17%
Binning points: 18%
Binning points: 19%
Binning points: 20%
Binning points: 21%
Binning points: 22%
Binning points: 23%
Binning points: 24%
Binning points: 25%
Binning points: 26%
Binning points: 27%
Binning points: 28%
Binning points: 29%
Binning points: 30%
Binning points: 31%
Binning points: 32%
Binning points: 33%
Binning points: 34%
Binning points: 35%
Binning points: 36%
Binning points: 37%
Binning points: 38%
Binning points: 39%
Binning points: